https://huggingface.co/bert-base-multilingual-cased

In [1]:
!pip install transformers

     |████████████████████████████████| 2.1MB 12.7MB/s 
     |████████████████████████████████| 3.3MB 60.1MB/s 
     |████████████████████████████████| 901kB 54.8MB/s 


In [2]:
from transformers import BertTokenizer, TFBertModel
#tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased')
model = TFBertModel.from_pretrained("bert-base-multilingual-cased")

Some layers from the model checkpoint at bert-base-multilingual-cased were not used when initializing TFBertModel: ['nsp___cls', 'mlm___cls']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at bert-base-multilingual-cased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [3]:
import os
import os
import re
import json
import string
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tokenizers import BertWordPieceTokenizer
from transformers import BertTokenizer, TFBertModel, BertConfig

max_len = 384
#configuration = BertConfig()  # default parameters and configuration for BERT

slow_tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased')
save_path = "bert-base-multilingual-cased/"
if not os.path.exists(save_path):
    os.makedirs(save_path)
slow_tokenizer.save_pretrained(save_path)

# Load the fast tokenizer from saved file
tokenizer = BertWordPieceTokenizer("bert-base-multilingual-cased/vocab.txt", lowercase=False, strip_accents=False)

In [4]:
from google.colab import drive 
drive.mount('/content/mnt',force_remount=True)

Mounted at /content/mnt


In [5]:
import tensorflow as tf
from tensorflow.keras import callbacks

In [6]:
class Sample:
    def __init__(self, question, context, start_char_idx=None, answer_text=None, all_answers=None):
        self.question = question
        self.context = context
        self.start_char_idx = start_char_idx
        self.answer_text = answer_text
        self.all_answers = all_answers
        self.skip = False
        self.start_token_idx = -1
        self.end_token_idx = -1

    def preprocess(self):
        # clean context and question
        context = " ".join(str(self.context).split())
        question = " ".join(str(self.question).split())
        # tokenize context and question
        tokenized_context = tokenizer.encode(context)
        print(tokenized_context)
        tokenized_question = tokenizer.encode(question)
        print(tokenized_question)
        # if this is validation or training sample, preprocess answer
        if self.answer_text is not None:
            answer = " ".join(str(self.answer_text).split())
            # check if end character index is in the context
            end_char_idx = self.start_char_idx + len(answer)
            if end_char_idx >= len(context):
                self.skip = True
                return
            # mark all the character indexes in context that are also in answer     
            is_char_in_ans = [0] * len(context)
            for idx in range(self.start_char_idx, end_char_idx):
                is_char_in_ans[idx] = 1
            ans_token_idx = []
            # find all the tokens that are in the answers
            for idx, (start, end) in enumerate(tokenized_context.offsets):  #.이부분 많이 수정함   #tokenized_context: 토큰이 인코딩된 숫자들의 리스트
                if len(tokenized_context) > 0:
                    ans_token_idx.append(idx)
            if len(ans_token_idx) == 0:
                self.skip = True
                return
            # get start and end token indexes
            self.start_token_idx = ans_token_idx[0]
            self.end_token_idx = ans_token_idx[-1]
        # create inputs as usual
        input_ids = tokenized_context.ids + tokenized_question.ids[1:]
        token_type_ids = [0] * len(tokenized_context.ids) + [1] * len(tokenized_question.ids[1:])
        attention_mask = [1] * len(input_ids)
        padding_length = max_seq_length - len(input_ids)
        # add padding if necessary
        if padding_length > 0:
            input_ids = input_ids + ([0] * padding_length)
            attention_mask = attention_mask + ([0] * padding_length)
            token_type_ids = token_type_ids + ([0] * padding_length)
        elif padding_length < 0:
            self.skip = True
            return
        self.input_word_ids = input_ids
        self.input_type_ids = token_type_ids
        self.input_mask = attention_mask
        self.context_token_to_char = tokenized_context.offsets

In [7]:
def create_squad_examples(raw_data):
    squad_examples = []
    for item in raw_data["data"]:
        for para in item["paragraphs"]:
            context = para["context"]
            for qa in para["qas"]:
                question = qa["question"]
                if "answers" in qa:
                    answer_text = qa["answers"][0]["text"]
                    all_answers = [_["text"] for _ in qa["answers"]]
                    start_char_idx = qa["answers"][0]["answer_start"]
                    squad_eg = Sample(question, context, start_char_idx, answer_text, all_answers)
                else:
                    squad_eg = Sample(question, context)
                squad_eg.preprocess()
                squad_examples.append(squad_eg)
    return squad_examples


def create_inputs_targets(squad_examples):
    dataset_dict = {
        "input_word_ids": [],
        "input_type_ids": [],
        "input_mask": [],
        "start_token_idx": [],
        "end_token_idx": [],
    }
    for item in squad_examples:
        if item.skip == False:
            for key in dataset_dict:
                dataset_dict[key].append(getattr(item, key))
    for key in dataset_dict:
        dataset_dict[key] = np.array(dataset_dict[key])
    x = [dataset_dict["input_word_ids"],
         dataset_dict["input_mask"],
         dataset_dict["input_type_ids"]]
    y = [dataset_dict["start_token_idx"], dataset_dict["end_token_idx"]]
    return x, y

In [8]:
class ValidationCallback(callbacks.Callback):

    def normalize_text(self, text):
        # convert to lower case
        text = text.lower()
        # remove redundant whitespaces
        text = "".join(ch for ch in text if ch not in set(string.punctuation))
        # remove articles
        regex = re.compile(r"\b(a|an|the)\b", re.UNICODE)
        text = re.sub(regex, " ", text)
        text = " ".join(text.split())
        return text

    def __init__(self, x_eval, y_eval):
        self.x_eval = x_eval
        self.y_eval = y_eval

    def on_epoch_end(self, epoch, logs=None):
        # get the offsets of the first and last tokens of predicted answers
        pred_start, pred_end = self.model.predict(self.x_eval)
        count = 0
        eval_examples_no_skip = [_ for _ in eval_squad_examples if _.skip == False]
        # for every pair of offsets
        for idx, (start, end) in enumerate(zip(pred_start, pred_end)):
            # take the required Sample object with the ground-truth answers in it
            squad_eg = eval_examples_no_skip[idx]
            # use offsets to get back the span of text corresponding to
            # our predicted first and last tokens
            offsets = squad_eg.context_token_to_char
            start = np.argmax(start)
            end = np.argmax(end)
            if start >= len(offsets):
                continue
            pred_char_start = offsets[start][0]
            if end < len(offsets):
                pred_char_end = offsets[end][1]
                pred_ans = squad_eg.context[pred_char_start:pred_char_end]
            else:
                pred_ans = squad_eg.context[pred_char_start:]
            normalized_pred_ans = self.normalize_text(pred_ans)
            # clean the real answers
            normalized_true_ans = [self.normalize_text(_) for _ in squad_eg.all_answers]
            # check if the predicted answer is in an array of the ground-truth answers
            if normalized_pred_ans in normalized_true_ans:
                count += 1
        acc = count / len(self.y_eval[0])
        print(f"\nepoch={epoch + 1}, exact match score={acc:.2f}")  

Model: "functional_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
==================================================================================================
input_word_ids (InputLayer)     [(None, 384)]        0                                            
__________________________________________________________________________________________________
input_mask (InputLayer)         [(None, 384)]        0                                            
__________________________________________________________________________________________________
input_type_ids (InputLayer)     [(None, 384)]        0                                            
__________________________________________________________________________________________________
keras_layer (KerasLayer)        [(None, 768), (None, 109482241   input_word_ids[0][0]             
                                                                 input_mask[0][0]                 
                                                                 input_type_ids[0][0]             
__________________________________________________________________________________________________
start_logit (Dense)             (None, 384, 1)       768         keras_layer[0][1]                
__________________________________________________________________________________________________
end_logit (Dense)               (None, 384, 1)       768         keras_layer[0][1]                
__________________________________________________________________________________________________
flatten (Flatten)               (None, 384)          0           start_logit[0][0]                
__________________________________________________________________________________________________
flatten_1 (Flatten)             (None, 384)          0           end_logit[0][0]                  
__________________________________________________________________________________________________
activation (Activation)         (None, 384)          0           flatten[0][0]                    
__________________________________________________________________________________________________
activation_1 (Activation)       (None, 384)          0           flatten_1[0][0]                  
==================================================================================================
Total params: 109,483,777
Trainable params: 109,483,776
Non-trainable params: 1
__________________________________________________________________________________________________

In [9]:
val = '/content/mnt/MyDrive/Colab Notebooks/section4_project/mrc/validate.json'
train = '/content/mnt/MyDrive/Colab Notebooks/section4_project/mrc/train.json'
vocab = '/content/mnt/MyDrive/Colab Notebooks/section4_project/mrc/vocab.json'
test = '/content/mnt/MyDrive/Colab Notebooks/section4_project/mrc/test.json'

In [10]:
import json
import codecs

#json.load(codecs.open('sample.json', 'r', 'utf-8-sig'))
with open(train, encoding='utf-8-sig') as f:
    raw_train_data = json.load(f)

In [11]:
with open(val, encoding='utf-8-sig') as f:
    raw_eval_data = json.load(f)

In [12]:
with open(test, encoding='utf-8-sig') as f:
    raw_test_data = json.load(f)

In [14]:
raw_test_data['data'][0]

{'paragraphs': [{'context': '"6·13 지방선거 공식 선거운동이 시작된 후 맞은 첫 주말입니다. 여야 지도부가 총출동해 지원 유세를 벌였는데요. 각종 여론조사에서 우위를 보이고 있는 여당은 접전지역 공세에, 야당은 전통 지지층 결집에 주력했습니다. 정연욱 기자입니다. [리포트] 더불어민주당은 최대 접전 지역으로 꼽히는 경남 지역을 공략했습니다. 울산과 김해, 창원, 진주 등 이른바 &낙동강 벨트&를 순회하며, 침체된 지역 경제를 부각하고 야당 소속 단체장들의 책임론을 집중 제기했습니다. [추미애/더불어민주당 상임선대위원장 : 빨간당에 찍는 표는 다 적폐를 용인하고 적폐를 손들어주는 표가 될 겁니다. 결코 시민여러분에게 눈꼽만큼도 도움되지 않는 투표가 될 겁니다.] 자유한국당은 강세 지역인 서울 강남에서 출발해, 최대 승부처인 수도권에 집중했습니다. 지난 1년 동안 국민들의 생활이 더 어려워졌다며 현 정부의 경제 정책을 겨냥했고, 정책 수정을 위해서라도 제1야당을 지지해야한다고 강조했습니다. [홍준표/자유한국당 공동선대위원장 : 지방선거가 끝나고 나면 아마 부동산 보유세 폭탄이 곧 떨어질 겁니다. 보유세 폭탄이 떨어지면 제일 고통 받는 데가 강남 삼구입니다.] 바른미래당은 전남과 경북 지역 지원 유세를 통해 경제 실정을 지적하며 &유능한 경제 정당&을 내세웠고, 민주평화당은 호남에 지도부가 총출동해 &민주당 견제세력&을 부각하며 집중 유세를 이어갔습니다. 정의당은 광주와 경남 창원을 방문해 정의당이 한국당을 제치고 제1야당이 돼야 한다고 호소했습니다.첫 주말 유세에서 여당은 접전지역을 중심으로 초반 판세장악에 집중한 반면, 야당은 전통 지지층 결집으로 역전의 발판을 마련하는데 주력했습니다. KBS 뉴스 정연욱입니다."',
   'qas': [{'id': 'c1_234871-1',
     'question': '광주와 경남 창원을 방문해 한국당을 제치고 제1야당이 돼야 한다고 호소한 것은?'},
    {'id': 'c1_234872-1'

In [13]:
import tensorflow as tf
import numpy as np
from tensorflow.keras import layers

In [ ]:
raw_train_data

{'data': [{'paragraphs': [{'context': '[OSEN=강서정 기자] 걸그룹 우주소녀의 성소가 ‘설특집 2018 아이돌 육상·볼링·양궁·리듬체조·에어로빅 선수권 대회’(이하 아육대) 출연 소감을 전했다.성소는 15일 우주소녀 공식 인스타그램에 “먼저 설날 여러분 새해 복 많이 받으세요~ 이번 설날 ‘아육대’에서 오랜만에 리듬체조도 하게 되었는데 저한테 기대 많이 했는데 이번에 좀 실망을 드린 것 같아요. 그래도 이번에 즐기면서 재밌게 했어요. 너무 좋은 추억이 되었어요!”라는 글을 게재했다.이어 “항상 하면서 좋은 언니, 동생, 친구 만날 수 있고 선생님도 뵐 수 있었고! 저와 2년 동안 함께 고생하셨던 선생님 그리고 이번에 함께 하셨던 선수 분들 고생 많았어요! 너무 축하하고 모두모두 설날 해피!! 우리 팬분들도 걱정 많이 하셨는데 너무 걱정 안해도 돼요 이제. 우정 너무 고마워요”라고 고마운 마음을 전했다.성소는 이날 방송된 MBC ‘아육대’ 리듬체조 경기에 출전했다. 원조 ‘리듬체조 여신’ 성소가 이번에도 기대를 모았는데 발레경력 7년의 에이프릴의 레이첼이 완벽한 경기를 선보이며 성소를 제치고 우승했다. /kangsj@osen.co.kr[사진] 우주소녀 인스타그램',
     'qas': [{'answers': [{'answer_start': 450, 'text': '아육대'}],
       'classtype': 'work_who',
       'id': 'm5_306497-1',
       'question': '걸그룹 우주소녀의 성소가 이 프로그램에 출연해 리듬체조 경기에 출전했는데, 이 프로그램의 이름은?'}]}],
   'source': 6,
   'title': '649'},
  {'paragraphs': [{'context': '신앙생활을 하다 보면 영적 침체기가 찾아옵니다. 저 또한 영적 침체기를 겪으며 어떻게 극복할 수 있을까 고민에 빠졌던 적이 있습니다. 그러던 중 새벽운동을 마치고 집으로 돌아오는 길에 한

In [16]:
from tensorflow import keras

bert_layer = TFBertModel.from_pretrained("bert-base-multilingual-cased", trainable=False) 가 안 되는 이유:

마운트 해서. 즉 tfbertmodel은 마운트 안 된 위치에 저장되어 있는데, 내가 구글 드라이브를 마운트 해서 그 이후로는 여기서 못 찾음. 따라서 마운트 전에 model을 다운 받고 쓰면 됨

In [17]:
#input_word_ids = tf.keras.layers.Input(shape=(max_seq_length,), dtype=tf.int32, name='input_word_ids')
#input_mask = tf.keras.layers.Input(shape=(max_seq_length,), dtype=tf.int32, name='input_mask')
#input_type_ids = tf.keras.layers.Input(shape=(max_seq_length,), dtype=tf.int32, name='input_type_ids')
bert_layer = model
#pooled_output, sequence_output = bert_layer([input_word_ids, input_mask, input_type_ids])

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module, class, method, function, traceback, frame, or code object was expected, got cython_function_or_method
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module, class, method, function, traceback, frame, or code object was expected, got cython_function_or_method
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Cause: while/else statement not yet supported
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Cause: while/else statement not yet supported
To silence this warning, decorate the function with @tf.autograph.experi

In [15]:
max_seq_length = 384  #최대 512
train_squad_examples = create_squad_examples(raw_train_data)
x_train, y_train = create_inputs_targets(train_squad_examples)
print(f"{len(train_squad_examples)} training points created.")
eval_squad_examples = create_squad_examples(raw_eval_data)
x_eval, y_eval = create_inputs_targets(eval_squad_examples)
print(f"{len(eval_squad_examples)} evaluation points created.")



스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
Encoding(num_tokens=31, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=500, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=29, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=496, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=40, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=496, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=35, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=496, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding

In [ ]:
"""
start_logits = layers.Dense(1, name="start_logit", use_bias=False)(sequence_output)
start_logits = layers.Flatten()(start_logits)
end_logits = layers.Dense(1, name="end_logit", use_bias=False)(sequence_output)
end_logits = layers.Flatten()(end_logits)
start_probs = layers.Activation(keras.activations.softmax)(start_logits)
end_probs = layers.Activation(keras.activations.softmax)(end_logits)
model = keras.Model(inputs=[input_word_ids, input_mask, input_type_ids], outputs=[start_probs, end_probs])
loss = keras.losses.SparseCategoricalCrossentropy(from_logits=False)
optimizer = keras.optimizers.Adam(lr=1e-5, beta_1=0.9, beta_2=0.98, epsilon=1e-9)
model.compile(optimizer=optimizer, loss=[loss, loss])
model.summary()
"""

In [36]:
model.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 384)]        0                                            
__________________________________________________________________________________________________
input_3 (InputLayer)            [(None, 384)]        0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 384)]        0                                            
__________________________________________________________________________________________________
tf_bert_model (TFBertModel)     TFBaseModelOutputWit 177853440   input_1[0][0]                    
                                                                 input_3[0][0]                

In [18]:
def create_model():
    ## BERT encoder
    encoder = bert_layer #TFBertModel.from_pretrained("bert-base-uncased")

    ## QA Model
    input_ids = layers.Input(shape=(max_len,), dtype=tf.int32)
    token_type_ids = layers.Input(shape=(max_len,), dtype=tf.int32)
    attention_mask = layers.Input(shape=(max_len,), dtype=tf.int32)
    embedding = encoder(
        input_ids, token_type_ids=token_type_ids, attention_mask=attention_mask
    )[0]

    start_logits = layers.Dense(1, name="start_logit", use_bias=False)(embedding)
    start_logits = layers.Flatten()(start_logits)

    end_logits = layers.Dense(1, name="end_logit", use_bias=False)(embedding)
    end_logits = layers.Flatten()(end_logits)

    start_probs = layers.Activation(keras.activations.softmax)(start_logits)
    end_probs = layers.Activation(keras.activations.softmax)(end_logits)

    model = keras.Model(
        inputs=[input_ids, token_type_ids, attention_mask],
        outputs=[start_probs, end_probs],
    )
    loss = keras.losses.SparseCategoricalCrossentropy(from_logits=False)
    optimizer = keras.optimizers.Adam(lr=1e-5, beta_1=0.9, beta_2=0.98, epsilon=1e-9)
    model.compile(optimizer=optimizer, loss=[loss, loss])
    return model
model = create_model()

In [ ]:
history = model.fit(x_train, y_train, epochs=2, batch_size=8, callbacks=[ValidationCallback(x_eval, y_eval)])
model.save_weights("./mrc_weights.h5")

In [42]:
path = '/MyDrive/Colab Notebooks/section4_project'

In [21]:
import os
os.getcwd()

'/content'

In [43]:
weight_path = os.path.join(path, 'mrc_weights.h5')

In [44]:
weight_path

'/MyDrive/Colab Notebooks/section4_project/mrc_weights.h5'

In [46]:
cd MyDrive/Colab Notebooks/section4_project

/content/mnt/MyDrive/Colab Notebooks/section4_project


In [48]:
!ls

 2.wav		   mrc		      preprocess.ipynb		 xlnet.ipynb
 korean_dialogue   MRC.ipynb	      QnAipynb
 korquad.ipynb	  'mrc_weights .h5'   speech_recognition.ipynb
 ksponspeech1	   pororo.ipynb       wake-word.ipynb


In [49]:
model.load_weights('mrc_weights .h5')

In [50]:
model.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 384)]        0                                            
__________________________________________________________________________________________________
input_3 (InputLayer)            [(None, 384)]        0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 384)]        0                                            
__________________________________________________________________________________________________
tf_bert_model (TFBertModel)     TFBaseModelOutputWit 177853440   input_1[0][0]                    
                                                                 input_3[0][0]                

In [52]:
data = raw_test_data

In [53]:
test_samples = create_squad_examples(data)
x_test, _ = create_inputs_targets(test_samples)
pred_start, pred_end = model.predict(x_test)


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
Encoding(num_tokens=660, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=28, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=660, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=37, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=972, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=17, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=972, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding(num_tokens=14, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
Encoding

In [64]:
attrs = vars(test_sample)
print(attrs)

{'question': '광주와 경남 창원을 방문해 한국당을 제치고 제1야당이 돼야 한다고 호소한 것은?', 'context': '"6·13 지방선거 공식 선거운동이 시작된 후 맞은 첫 주말입니다. 여야 지도부가 총출동해 지원 유세를 벌였는데요. 각종 여론조사에서 우위를 보이고 있는 여당은 접전지역 공세에, 야당은 전통 지지층 결집에 주력했습니다. 정연욱 기자입니다. [리포트] 더불어민주당은 최대 접전 지역으로 꼽히는 경남 지역을 공략했습니다. 울산과 김해, 창원, 진주 등 이른바 &낙동강 벨트&를 순회하며, 침체된 지역 경제를 부각하고 야당 소속 단체장들의 책임론을 집중 제기했습니다. [추미애/더불어민주당 상임선대위원장 : 빨간당에 찍는 표는 다 적폐를 용인하고 적폐를 손들어주는 표가 될 겁니다. 결코 시민여러분에게 눈꼽만큼도 도움되지 않는 투표가 될 겁니다.] 자유한국당은 강세 지역인 서울 강남에서 출발해, 최대 승부처인 수도권에 집중했습니다. 지난 1년 동안 국민들의 생활이 더 어려워졌다며 현 정부의 경제 정책을 겨냥했고, 정책 수정을 위해서라도 제1야당을 지지해야한다고 강조했습니다. [홍준표/자유한국당 공동선대위원장 : 지방선거가 끝나고 나면 아마 부동산 보유세 폭탄이 곧 떨어질 겁니다. 보유세 폭탄이 떨어지면 제일 고통 받는 데가 강남 삼구입니다.] 바른미래당은 전남과 경북 지역 지원 유세를 통해 경제 실정을 지적하며 &유능한 경제 정당&을 내세웠고, 민주평화당은 호남에 지도부가 총출동해 &민주당 견제세력&을 부각하며 집중 유세를 이어갔습니다. 정의당은 광주와 경남 창원을 방문해 정의당이 한국당을 제치고 제1야당이 돼야 한다고 호소했습니다.첫 주말 유세에서 여당은 접전지역을 중심으로 초반 판세장악에 집중한 반면, 야당은 전통 지지층 결집으로 역전의 발판을 마련하는데 주력했습니다. KBS 뉴스 정연욱입니다."', 'start_char_idx': None, 'answer_text': None, 'all_answers': None, 'skip': True,

In [74]:
raw_test_data['data'][0]['paragraphs'][0]

{'context': '"6·13 지방선거 공식 선거운동이 시작된 후 맞은 첫 주말입니다. 여야 지도부가 총출동해 지원 유세를 벌였는데요. 각종 여론조사에서 우위를 보이고 있는 여당은 접전지역 공세에, 야당은 전통 지지층 결집에 주력했습니다. 정연욱 기자입니다. [리포트] 더불어민주당은 최대 접전 지역으로 꼽히는 경남 지역을 공략했습니다. 울산과 김해, 창원, 진주 등 이른바 &낙동강 벨트&를 순회하며, 침체된 지역 경제를 부각하고 야당 소속 단체장들의 책임론을 집중 제기했습니다. [추미애/더불어민주당 상임선대위원장 : 빨간당에 찍는 표는 다 적폐를 용인하고 적폐를 손들어주는 표가 될 겁니다. 결코 시민여러분에게 눈꼽만큼도 도움되지 않는 투표가 될 겁니다.] 자유한국당은 강세 지역인 서울 강남에서 출발해, 최대 승부처인 수도권에 집중했습니다. 지난 1년 동안 국민들의 생활이 더 어려워졌다며 현 정부의 경제 정책을 겨냥했고, 정책 수정을 위해서라도 제1야당을 지지해야한다고 강조했습니다. [홍준표/자유한국당 공동선대위원장 : 지방선거가 끝나고 나면 아마 부동산 보유세 폭탄이 곧 떨어질 겁니다. 보유세 폭탄이 떨어지면 제일 고통 받는 데가 강남 삼구입니다.] 바른미래당은 전남과 경북 지역 지원 유세를 통해 경제 실정을 지적하며 &유능한 경제 정당&을 내세웠고, 민주평화당은 호남에 지도부가 총출동해 &민주당 견제세력&을 부각하며 집중 유세를 이어갔습니다. 정의당은 광주와 경남 창원을 방문해 정의당이 한국당을 제치고 제1야당이 돼야 한다고 호소했습니다.첫 주말 유세에서 여당은 접전지역을 중심으로 초반 판세장악에 집중한 반면, 야당은 전통 지지층 결집으로 역전의 발판을 마련하는데 주력했습니다. KBS 뉴스 정연욱입니다."',
 'qas': [{'id': 'c1_234871-1',
   'question': '광주와 경남 창원을 방문해 한국당을 제치고 제1야당이 돼야 한다고 호소한 것은?'},
  {'id': 'c1_234872-1', 'question': '더불어민주당은

In [57]:
for idx, (start, end) in enumerate(zip(pred_start, pred_end)):
    test_sample = test_samples[idx]
    offsets = test_sample.context_token_to_char
    
    start = np.argmax(start)
    end = np.argmax(end)
    pred_ans = None
    if start >= len(offsets):
        continue
    pred_char_start = offsets[start][0]
    if end < len(offsets):
        pred_ans = test_sample.context[pred_char_start:offsets[end][1]]
    else:
        pred_ans = test_sample.context[pred_char_start:]
    print("Q: " + test_sample.question)
    print("A: " + pred_ans)

AttributeError: ignored

In [89]:
raw_test_data['data'][0]

{'paragraphs': [{'context': '"6·13 지방선거 공식 선거운동이 시작된 후 맞은 첫 주말입니다. 여야 지도부가 총출동해 지원 유세를 벌였는데요. 각종 여론조사에서 우위를 보이고 있는 여당은 접전지역 공세에, 야당은 전통 지지층 결집에 주력했습니다. 정연욱 기자입니다. [리포트] 더불어민주당은 최대 접전 지역으로 꼽히는 경남 지역을 공략했습니다. 울산과 김해, 창원, 진주 등 이른바 &낙동강 벨트&를 순회하며, 침체된 지역 경제를 부각하고 야당 소속 단체장들의 책임론을 집중 제기했습니다. [추미애/더불어민주당 상임선대위원장 : 빨간당에 찍는 표는 다 적폐를 용인하고 적폐를 손들어주는 표가 될 겁니다. 결코 시민여러분에게 눈꼽만큼도 도움되지 않는 투표가 될 겁니다.] 자유한국당은 강세 지역인 서울 강남에서 출발해, 최대 승부처인 수도권에 집중했습니다. 지난 1년 동안 국민들의 생활이 더 어려워졌다며 현 정부의 경제 정책을 겨냥했고, 정책 수정을 위해서라도 제1야당을 지지해야한다고 강조했습니다. [홍준표/자유한국당 공동선대위원장 : 지방선거가 끝나고 나면 아마 부동산 보유세 폭탄이 곧 떨어질 겁니다. 보유세 폭탄이 떨어지면 제일 고통 받는 데가 강남 삼구입니다.] 바른미래당은 전남과 경북 지역 지원 유세를 통해 경제 실정을 지적하며 &유능한 경제 정당&을 내세웠고, 민주평화당은 호남에 지도부가 총출동해 &민주당 견제세력&을 부각하며 집중 유세를 이어갔습니다. 정의당은 광주와 경남 창원을 방문해 정의당이 한국당을 제치고 제1야당이 돼야 한다고 호소했습니다.첫 주말 유세에서 여당은 접전지역을 중심으로 초반 판세장악에 집중한 반면, 야당은 전통 지지층 결집으로 역전의 발판을 마련하는데 주력했습니다. KBS 뉴스 정연욱입니다."',
   'qas': [{'id': 'c1_234871-1',
     'question': '광주와 경남 창원을 방문해 한국당을 제치고 제1야당이 돼야 한다고 호소한 것은?'},
    {'id': 'c1_234872-1'

In [91]:
test_data = {"data": [raw_test_data['data'][0]]}

In [56]:
test_samples = create_squad_examples(test_data)
x_test, _ = create_inputs_targets(test_samples)
pred_start, pred_end = model.predict(x_test)
for idx, (start, end) in enumerate(zip(pred_start, pred_end)):
    test_sample = test_samples[idx]
    offsets = test_sample.context_token_to_char
    start = np.argmax(start)
    end = np.argmax(end)
    pred_ans = None
    if start >= len(offsets):
        continue
    pred_char_start = offsets[start][0]
    if end < len(offsets):
        pred_ans = test_sample.context[pred_char_start:offsets[end][1]]
    else:
        pred_ans = test_sample.context[pred_char_start:]
    print("Q: " + test_sample.question)
    print("A: " + pred_ans)

NameError: ignored